# IPOPT in CoCalc running via the "Anaconda 2019" kernel

https://coin-or.github.io/Ipopt/

## IPOPT + scipy

In [1]:
from scipy.optimize import rosen, rosen_der
from ipopt import minimize_ipopt
x0 = [1.3, 0.7, 0.8, 1.9, 1.2]
res = minimize_ipopt(rosen, x0, jac=rosen_der)
print(res)

     fun: 2.1457658477147543e-18
    info: {'x': array([1., 1., 1., 1., 1.]), 'g': array([], dtype=float64), 'obj_val': 2.1457658477147543e-18, 'mult_g': array([], dtype=float64), 'mult_x_L': array([0., 0., 0., 0., 0.]), 'mult_x_U': array([0., 0., 0., 0., 0.]), 'status': 0, 'status_msg': b'Algorithm terminated successfully at a locally optimal point, satisfying the convergence tolerances (can be specified by options).'}
 message: b'Algorithm terminated successfully at a locally optimal point, satisfying the convergence tolerances (can be specified by options).'
    nfev: 200
     nit: 37
    njev: 39
  status: 0
 success: True
       x: array([1., 1., 1., 1., 1.])


## IPOPT + PyOMO

- http://www.pyomo.org/

In [2]:
from pyomo.environ import *

# Concrete Model
model = ConcreteModel(name="Wyndor")

products = ['drs', 'wdw']

bounds_dict = {'drs': (0, 4), 'wdw': (0, 6)}


def bounds_rule(model, product):
    return (bounds_dict[product])


model.x = Var(products, domain=Reals, bounds=bounds_rule)

# Objective
model.profit = Objective(expr=126.0 * model.x['drs'] -
                         9.0 * model.x['drs']**2 + 182.0 * model.x['wdw'] -
                         13.0 * model.x['wdw']**2.0,
                         sense=maximize)

# Constraints
model.Constraint3 = Constraint(
    expr=3.0 * model.x['drs'] + 2.0 * model.x['wdw'] <= 18)

display(model)

Model Wyndor

  Variables:
    x : Size=2, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
        drs :     0 :  None :     4 : False :  True :  Reals
        wdw :     0 :  None :     6 : False :  True :  Reals

  Objectives:
    profit : Size=1, Index=None, Active=True
ERROR: evaluating object as numeric value: x[drs]
        (object: <class 'pyomo.core.base.var._GeneralVarData'>)
    No value for uninitialized NumericValue object x[drs]
ERROR: evaluating object as numeric value: profit
        (object: <class 'pyomo.core.base.objective.SimpleObjective'>)
    No value for uninitialized NumericValue object x[drs]
        Key : Active : Value
        None :   None :  None

  Constraints:
    Constraint3 : Size=1
ERROR: evaluating object as numeric value: x[drs]
        (object: <class 'pyomo.core.base.var._GeneralVarData'>)
    No value for uninitialized NumericValue object x[drs]
        Key : Lower : Body : Upper
        None :  None : None :  None


In [3]:
# Solve
solver = SolverFactory('ipopt')
solver.solve(model)

{'Problem': [{'Lower bound': -inf, 'Upper bound': inf, 'Number of objectives': 1, 'Number of constraints': 1, 'Number of variables': 2, 'Sense': 'unknown'}], 'Solver': [{'Status': 'ok', 'Message': 'Ipopt 3.12.12\\x3a Optimal Solution Found', 'Termination condition': 'optimal', 'Id': 0, 'Error rc': 0, 'Time': 0.04679512977600098}], 'Solution': [OrderedDict([('number of solutions', 0), ('number of solutions displayed', 0)])]}

In [4]:
# display solution
import babel.numbers as numbers  # needed to display as currency
print("Profit = ",
      numbers.format_currency(1000 * model.profit(), 'USD', locale='en_US'))
print("Batches of Doors = {:1.2f}".format(model.x['drs']()))
print("Batches of Windows = {:1.2f}".format(model.x['wdw']()))

Profit =  $857,000.00
Batches of Doors = 2.67
Batches of Windows = 5.00
